# Modelo SEIR con Animación en Python

El modelo epidemiológico **SEIR** divide la población en cuatro compartimentos:

- $S(t)$: Susceptibles  
- $E(t)$: Expuesto
- $I(t)$: Infectados  
- $R(t)$: Recuperados/Removidos  

Las ecuaciones diferenciales son:

$$
\frac{dS}{dt} = -\beta S I, \quad
\frac{dE}{dt} = \beta SI - \sigma E, \quad
\frac{dI}{dt} = \sigma E - \gamma I, \quad
\frac{dR}{dt} = \gamma I
$$

Donde:
- $N = S + I + R$ es la población total (constante).  
- $\beta$ es la tasa de transmisión.  
- $\gamma$ es la tasa de recuperación.  
- $\sigma$ es la tasa de progresión de expuesto a infectado
- $R_0 = \frac{\beta}{\gamma}$ es el número reproductivo básico.  


In [50]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
from scipy.integrate import solve_ivp

# Parámetros del modelo

In [51]:
N = 500        # Población total
t = 100         #Transmisibilidad
k = 2           #Contactos de individuo infectado
dias_de_incubacion = 5
o = 1/dias_de_incubacion        #Tasa de progresion a infeccioso
b = k*t         
beta = b/N     # Tasa de transmisión
gamma = 0.1     # Tasa de recuperación
D = 1/gamma     # Duración promedio de la infección


# Condiciones iniciales

In [52]:
I0 = 1                # Infectados iniciales
E0 = 0                # Expuestos iniciales
R0 = 0                # Recuperados iniciales
S0 = N - I0 - R0 - E0 # Susceptibles iniciales

# Tiempo de simulación

In [53]:
t_max = 250
dt = 0.5   # Paso más grande para que la animación sea más rápida
t = np.linspace(0, t_max, int(t_max/dt))
step = 5

# Modelo SIR


In [54]:
def deriv(y, t, N, beta, gamma,o):
    S, E, I, R = y
    dSdt = -beta * S * I /N
    dEdt = beta * S * I/N - (o * E)
    dIdt = (o * E) - gamma * I
    dRdt = gamma * I
    return dSdt, dEdt, dIdt, dRdt


# Metodos numericos para resolver el sistema


In [ ]:
# Euler simple
def euler(N, beta, gamma,o, S0,E0, I0, R0, t, dt):
    S, E, I, R = [S0],[E0], [I0], [R0]
    for i in range(1, len(t)):
        dSdt, dEdt, dIdt, dRdt = deriv((S[-1], E[-1], I[-1], R[-1]), t[i], N, beta, gamma,o)
        S.append(S[-1] + dSdt*dt)
        E.append(E[-1] + dEdt*dt)
        I.append(I[-1] + dIdt*dt)
        R.append(R[-1] + dRdt*dt)
    return np.array(S), np.array(E), np.array(I), np.array(R)

# Runge-Kutta de orden 4 (RK4)
def rk4(N, beta, gamma,o, S0, E0, I0, R0, t, dt):
    S,E, I, R = [S0], [E0], [I0], [R0]
    for i in range(1, len(t)):
        Si, Ei, Ii, Ri = S[-1],E[-1], I[-1], R[-1]
        ti = t[i-1]
        dS1,dE1, dI1, dR1 = deriv((Si,Ei, Ii, Ri), ti, N, beta, gamma,o)
        dS2,dE2, dI2, dR2 = deriv((Si + dS1*dt/2,Ei + dE1*dt/2, Ii + dI1*dt/2, Ri + dR1*dt/2), ti+dt/2, N, beta, gamma,o)
        dS3,dE3, dI3, dR3 = deriv((Si + dS2*dt/2,Ei + dE2*dt/2, Ii + dI2*dt/2, Ri + dR2*dt/2), ti+dt/2, N, beta, gamma,o)
        dS4,dE4, dI4, dR4 = deriv((Si + dS3*dt,Ei + dE3*dt, Ii + dI3*dt, Ri + dR3*dt), ti+dt, N, beta, gamma,o)
        S_next = Si + (dt/6)*(dS1 + 2*dS2 + 2*dS3 + dS4)
        E_next = Ei + (dt/6)*(dE1 + 2*dE2 + 2*dE3 + dE4)
        I_next = Ii + (dt/6)*(dI1 + 2*dI2 + 2*dI3 + dI4)
        R_next = Ri + (dt/6)*(dR1 + 2*dR2 + 2*dR3 + dR4)
        S.append(S_next); E.append(E_next); I.append(I_next); R.append(R_next)
    return np.array(S),np.array(E), np.array(I), np.array(R)

# SciPy solve_ivp 
def rk45(N, beta, gamma,o, S0, E0, I0, R0, t):
    def seir(t, y): return deriv(y, t, N, beta, gamma,o)
    sol = solve_ivp(seir, (t[0], t[-1]), [S0, E0, I0, R0], t_eval=t, method='RK45')
    return sol.y[0], sol.y[1], sol.y[2], sol.y[3]


# Metodo Elegido

In [59]:
S,E,I,R = rk45(N,beta,gamma,o,S0,E0,I0,R0,t)

# Animacion

In [60]:
fig, ax = plt.subplots(figsize=(8,5))
ax.set_xlim(0, t_max)
ax.set_ylim(0, N)
ax.set_xlabel("Tiempo (días)")
ax.set_ylabel("Número de individuos")
ax.set_title("Modelo SEIR")

lineS, = ax.plot([], [], 'b-', lw=2, label="Susceptibles")
lineE, = ax.plot([], [], 'orange', lw=2, label="Expuestos") 
lineI, = ax.plot([], [], 'r-', lw=2, label="Infectados")
lineR, = ax.plot([], [], 'g-', lw=2, label="Recuperados")
ax.legend()

# Puntos en la punta de cada curva
pointS, = ax.plot([], [], 'bo')
pointE, =  ax.plot([], [], 'o', color='orange', markersize=6)
pointI, = ax.plot([], [], 'ro')
pointR, = ax.plot([], [], 'go')

# Textos dinámicos con estilo (más grandes y con círculo)
textS = ax.text(0,0,'',color='blue', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='blue', boxstyle='circle,pad=0.4'))
textE = ax.text(0,0,'',color='yellow', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='yellow', boxstyle='circle,pad=0.4'))
textI = ax.text(0,0,'',color='red', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='red', boxstyle='circle,pad=0.4'))
textR = ax.text(0,0,'',color='green', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='green', boxstyle='circle,pad=0.4'))

def init():
    lineS.set_data([], [])
    lineE.set_data([], [])
    lineI.set_data([], [])
    lineR.set_data([], [])
    pointS.set_data([], [])
    pointE.set_data([], [])
    pointI.set_data([], [])
    pointR.set_data([], [])
    textS.set_text('')
    textE.set_text('')
    textI.set_text('')
    textR.set_text('')
    return lineS, lineE, lineI, lineR, pointS, pointE, pointI, pointR, textS, textE, textI, textR

def update(frame):

    idx = frame * step
    if idx >= len(t):
        idx = len(t)-1
    
    # Actualizar curvas
    lineS.set_data(t[:idx], S[:idx])
    lineE.set_data(t[:idx], E[:idx])
    lineI.set_data(t[:idx], I[:idx])
    lineR.set_data(t[:idx], R[:idx])
    
    # Actualizar puntos
    pointS.set_data([t[idx]], [S[idx]])
    pointE.set_data([t[idx]], [E[idx]])
    pointI.set_data([t[idx]], [I[idx]])
    pointR.set_data([t[idx]], [R[idx]])
    
    # Actualizar textos (desplazados a la derecha)
    textS.set_position((t[idx]+2, S[idx]))
    textS.set_text(f"{S[idx]:.0f}")
    textE.set_position((t[idx]+2, E[idx]))
    textE.set_text(f"{E[idx]:.0f}")
    textI.set_position((t[idx]+2, I[idx]))
    textI.set_text(f"{I[idx]:.0f}")
    textR.set_position((t[idx]+2, R[idx]))
    textR.set_text(f"{R[idx]:.0f}")
    
    return lineS,lineE, lineI, lineR, pointS, pointE, pointI, pointR, textS, textE, textI, textR

ani = FuncAnimation(fig, update, frames=len(t)//step, init_func=init,
                    blit=True, interval=100, repeat=False)
plt.close()
HTML(ani.to_jshtml())


# Conclusiones

- La curva azul ($S$) muestra cómo disminuyen los susceptibles.  
- La curva roja ($I$) muestra el número de infectados, que sube, alcanza un máximo y luego baja.  
- La curva verde ($R$) muestra los recuperados, que siempre crecen.  

El texto dinámico en la animación muestra los parámetros del modelo:
- Población total $N$  
- Tasa de transmisión $\beta$  
- Tasa de recuperación $\gamma$  
- Duración promedio de la infección $D$  
- Número reproductivo básico $R_0 = \frac{\beta}{\gamma}$  

Este modelo permite entender cómo evoluciona una epidemia y cómo los parámetros afectan su dinámica.
